In [1]:
from Bio import SeqIO
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib.ticker import (MultipleLocator, AutoMinorLocator)
import io
import os
import base64
import sys
import json
import glob
import numpy as np

def plot_alignment(records, colors, actives, output_file):
    max_label_len = max(len(record.description) for record in records)
    fig_height = len(records) * 0.25
    fig_width = len(records[0].seq) * 0.21 + max_label_len * 0.03

    fig, ax = plt.subplots(figsize=(fig_width, fig_height), dpi=150)
    pad_left = max_label_len * 0.03
    ax.set_xlim(0.5, len(records[0].seq) + 0.5)
    ax.set_ylim(-0.5, len(records) - 0.5)

    ax.yaxis.set_major_locator(plt.NullLocator())
    ax.yaxis.set_minor_locator(plt.NullLocator())

    for i, record in enumerate(records):
        seq_name = record.description.split("/")[0].lower()
        label_weight = 'bold' if seq_name in actives else 'normal'
        ax.text(-pad_left, i, seq_name, ha='right', va='center', fontweight=label_weight, fontsize=10)

        for j, residue in enumerate(record.seq):
            color = colors[i][j]
            alpha_value = 0.3 if (seq_name in actives and residue == "-") else 1
            rect = plt.Rectangle((j + 0.5, i - 0.5), 1, 1, facecolor=color, edgecolor='none', alpha=alpha_value)
            ax.add_patch(rect)
            ax.text(j + 1, i, residue, ha='center', va='center', fontweight=label_weight, fontsize=12)

    ax.xaxis.set_major_locator(MultipleLocator(10))
    ax.xaxis.set_minor_locator(MultipleLocator(1))

    plt.gca().invert_yaxis()
    ax.xaxis.set_ticks_position("top")
    ax.tick_params(top=True, labeltop=True, bottom=False, labelbottom=False)
    ax.axvline(x=643.5, color='black', linestyle='-', linewidth=1)

    png_output_file = os.path.splitext(output_file)[0] + ".png"
    plt.savefig(png_output_file, dpi=150)

    with open(png_output_file, "rb") as f:
        img_data = base64.b64encode(f.read()).decode('utf-8')

    html = f'<html><body><div style="position: absolute; top: 0; left: 0;"><img src="data:image/png;base64,{img_data}" /></div></body></html>'

    with open(output_file, 'w') as f:
        f.write(html)


def color_alignment(fasta_file, actives, output_file):
    records = list(SeqIO.parse(fasta_file, "fasta"))
    color_map = {
        "orange": {"facecolor": "orange", "condition": lambda x: x < 50},
        "yellow": {"facecolor": "yellow", "condition": lambda x: 50 <= x < 70},
        "cyan": {"facecolor": "cyan", "condition": lambda x: 70 <= x < 90},
        "cornflowerblue": {"facecolor": "cornflowerblue", "condition": lambda x: x >= 90}
    }

    colors = []
    for i, record in enumerate(records):
        seq_colors = []
        seq_name = record.description.split("/")[0].lower()

        try:
            json_files = glob.glob(f"{seq_name}_4x2/{seq_name}_4x2_scores_rank_001_*.json")
            json_file = json_files[0]
        except IndexError:
            print(f"No JSON file found for {seq_name}")
            continue

        with open(json_file) as json_file_handle:
            print('loading ', json_file)
            data = json.load(json_file_handle)
            values = data.get("plddt", [])
        
        alignment_sequence = str(record.seq).replace("-", "")
        values = values[:len(alignment_sequence)]
        
        value_index = 0
        for j, residue in enumerate(record.seq):
            if residue == "-":
                seq_colors.append("silver" if seq_name in actives else "white")
            else:
                residue_value = values[value_index] if value_index < len(values) else None
                color_key = next(
                    (color for color, attr in color_map.items() if attr["condition"](residue_value)), "white"
                )
                seq_colors.append(color_map.get(color_key, {}).get("facecolor", "white"))
                value_index += 1

        colors.append(seq_colors)

    plot_alignment(records, colors, actives, output_file)


def color_alignment2(fasta_file, actives, output_file):
    records = list(SeqIO.parse(fasta_file, "fasta"))

    # Pre-fetch all JSON data into a dictionary
    json_data = {}
    for record in records:
        seq_name = record.description.split("/")[0].lower()
        try:
            json_files = glob.glob(f"{seq_name}_4x2/{seq_name}_4x2_scores_rank_001_*.json")
            json_file = json_files[0]
            with open(json_file) as json_file_handle:
                json_data[seq_name] = json.load(json_file_handle).get("plddt", [])
        except IndexError:
            print(f"No JSON file found for {seq_name}")

    colors = []
    for record in records:
        seq_name = record.description.split("/")[0].lower()
        values = json_data.get(seq_name, [])
        alignment_sequence = str(record.seq).replace("-", "")
        
        # Vectorize color computations using Numpy
        np_values = np.array(values[:len(alignment_sequence)], dtype=float)
        conditions = [50, 70, 90]
        color_keys = ["orange", "yellow", "cyan", "cornflowerblue"]

        # Vectorized color matching
        color_indices = np.digitize(np_values, conditions)
        np_colors = np.array([color_keys[i] for i in color_indices])

        # Fill in the gaps and '-' with appropriate colors
        colors_list = ["silver" if seq_name in actives else "white"] * len(record.seq)
        value_index = 0
        for j, residue in enumerate(record.seq):
            if residue != "-":
                colors_list[j] = np_colors[value_index]
                value_index += 1

        colors.append(colors_list)

    plot_alignment(records, colors, actives, output_file)

        
# Test example
#fasta_file = "nylc.test.mafft.fasta"
#actives = ["nylc", "nyl04", "nyl10"]
#output_file = "nylc.test.mafft.plddt.html"
#color_alignment(fasta_file, actives, output_file)

# Usage
fasta_file = "nylc_diversity_panel.mafft.fasta"
actives = ["nylc", "nyl04", "nyl10", "nyl11", "nyl12", "nyl13", "nyl14", 
           "nyl15", "nyl16", "nyl18", "nyl25", "nyl30", "nyl32", "nyl37",
           "nyl40", "nyl41", "nyl45", "nyl47", "nyl48", "nyl50", "nyl68",
           "nyl71", "nyl73", "nyl74", "nyl76", "nyl77", "nyl80", "nyl82",
           "nyl85", "nyl87", "nyl88", "nyl92", "nyl94"]
output_file = "nylc_diversity_panel.mafft_alignment_colored_by_plddt_20230914_jmp.html"
color_alignment(fasta_file, actives, output_file)

loading  nylc_4x2/nylc_4x2_scores_rank_001_alphafold2_multimer_v3_model_2_seed_000.json
loading  nyl01_4x2/nyl01_4x2_scores_rank_001_alphafold2_multimer_v3_model_4_seed_000.json
loading  nyl02_4x2/nyl02_4x2_scores_rank_001_alphafold2_multimer_v3_model_5_seed_000.json
loading  nyl03_4x2/nyl03_4x2_scores_rank_001_alphafold2_multimer_v3_model_2_seed_000.json
loading  nyl04_4x2/nyl04_4x2_scores_rank_001_alphafold2_multimer_v3_model_2_seed_000.json
loading  nyl05_4x2/nyl05_4x2_scores_rank_001_alphafold2_multimer_v3_model_1_seed_000.json
loading  nyl06_4x2/nyl06_4x2_scores_rank_001_alphafold2_multimer_v3_model_3_seed_000.json
loading  nyl07_4x2/nyl07_4x2_scores_rank_001_alphafold2_multimer_v3_model_5_seed_000.json
loading  nyl08_4x2/nyl08_4x2_scores_rank_001_alphafold2_multimer_v3_model_1_seed_000.json
loading  nyl09_4x2/nyl09_4x2_scores_rank_001_alphafold2_multimer_v3_model_3_seed_000.json
loading  nyl10_4x2/nyl10_4x2_scores_rank_001_alphafold2_multimer_v3_model_2_seed_000.json
loading  nyl

loading  nyl93_4x2/nyl93_4x2_scores_rank_001_alphafold2_multimer_v3_model_4_seed_000.json
loading  nyl94_4x2/nyl94_4x2_scores_rank_001_alphafold2_multimer_v3_model_4_seed_000.json
loading  nyl95_4x2/nyl95_4x2_scores_rank_001_alphafold2_multimer_v3_model_3_seed_000.json
